In [1]:
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
pd.set_option('display.float_format', lambda x: '%.4f' % x)
import seaborn as sns
sns.set_context("paper", font_scale=1.3)
sns.set_style('white')
import warnings
warnings.filterwarnings('ignore')
import datetime
import matplotlib.ticker as tkr
import math
import keras
import torch
import pickle
from time import time
from IPython.display import display
from IPython.display import SVG
from sklearn.model_selection import train_test_split
import pytorch_lightning as pl
from pytorch_forecasting.metrics import SMAPE, PoissonLoss, QuantileLoss
from pytorch_lightning.callbacks import EarlyStopping, LearningRateMonitor
from pytorch_lightning.loggers import TensorBoardLogger
from pytorch_forecasting import TimeSeriesDataSet, TemporalFusionTransformer
from pytorch_forecasting.metrics import MAE
from numpy.random import seed
seed(20)
import tensorflow as tf
from keras import backend as K
from keras.wrappers.scikit_learn import KerasRegressor
from sklearn import preprocessing
from sklearn.feature_selection import SelectPercentile, f_regression, mutual_info_regression, SelectKBest
pd.set_option('display.max_columns', None)

C:\Users\Austin\Anaconda3\lib\site-packages\statsmodels\tools\_testing.py:19: FutureWarning: pandas.util.testing is deprecated. Use the functions in the public API at pandas.testing instead.
  import pandas.util.testing as tm


In [2]:
class Logger(object):
    def __init__(self):
        self.terminal = sys.stdout
        self.log = open("All_Classifierq.log", "a")

    def write(self, message):
        self.terminal.write(message)
        self.log.write(message)  

    def flush(self):
        #this flush method is needed for python 3 compatibility.
        #this handles the flush command by doing nothing.
        #you might want to specify some extra behavior here.
        self.acquire()
        try:
            if self.stream and hasattr(self.stream, "flush"):
                self.stream.flush()
        finally:
            self.release()

import sys

def spcc(y_true, y_pred, **kwargs):
    corr, _ = pearsonr(y_true, y_pred)
    return corr
    
    
def windowed_dataset(series, window_size, batch_size, shuffle_buffer):
    dataset = tf.data.Dataset.from_tensor_slices(series)
    dataset = dataset.window(window_size + 1, shift=1, drop_remainder=True)
    dataset = dataset.flat_map(lambda window: window.batch(window_size + 1))
    #dataset = dataset.shuffle(shuffle_buffer).map(lambda window: (window[:-1], window[-1]))
    dataset = dataset.map(lambda window: (window[:-1], window[-1]))
    dataset = dataset.batch(batch_size).prefetch(1)
    return dataset
    
#Takes a dataframe with the holiday field and returns encoded dataframe.
def onehotholiday(select):
    X_2 = select[['Holiday']]
    # TODO: create a OneHotEncoder object, and fit it to all of X
    # 1. INSTANTIATE
    enc = preprocessing.OneHotEncoder(sparse=False)
    
    # 2. FIT
    enc.fit(X_2)
    
    # 3. Transform
    onehotlabels = enc.transform(X_2)
    # creating a list of column names 
    column_values = []
    for i in range(np.shape(onehotlabels)[1]):
            column_values.append('A'+str(i))

    # creating the dataframe 
    onehotholiday = pd.DataFrame(data = onehotlabels,columns = column_values)

    dataset = select.drop(columns=['Holiday'])
    dataset = select.join(onehotholiday)
    df1 = dataset.pop('2to5')
    dataset['2to5']=df1 # add b series as a 'new' column
    dataset2=dataset
    dataset2 = dataset2.drop(columns=['Holiday'])
    return dataset2
    
def onehotholidaydiff(select, col):
    X_2 = select[['Holiday']]
    # TODO: create a OneHotEncoder object, and fit it to all of X
    # 1. INSTANTIATE
    enc = preprocessing.OneHotEncoder(sparse=False)
    
    # 2. FIT
    enc.fit(X_2)
    
    # 3. Transform
    onehotlabels = enc.transform(X_2)
    # creating a list of column names 
    column_values = []
    for i in range(np.shape(onehotlabels)[1]):
            column_values.append('A'+str(i))

    # creating the dataframe 
    onehotholiday = pd.DataFrame(data = onehotlabels,columns = column_values)

    dataset = select.drop(columns=['Holiday'])
    dataset = select.join(onehotholiday)
    df1 = dataset.pop(col)
    dataset[col]=df1 # add b series as a 'new' column
    dataset2=dataset
    dataset2 = dataset2.drop(columns=['Holiday'])
    return dataset2
    
    

def diff_add_lookback(dataset, look_back, df, col):
    for i in range(len(dataset)-look_back):
        a = dataset[i:(i+look_back)][col]
        a = a.values
        for j in range(len(a)):
            df[j][i]= a[j]
    return df

def add_lookback(dataset, look_back, df):
    for i in range(len(dataset)-look_back):
        a = dataset[i:(i+look_back)]['2to5']
        a = a.values
        for j in range(len(a)):
            df[j][i]= a[j]
    return df

Dense Model

In [ ]:
dense = tf.keras.models.Sequential([
    tf.keras.layers.Lambda(lambda x: tf.expand_dims(x, axis=-1),
                      input_shape=[None]),
    tf.keras.layers.Dense(64),
    keras.layers.Dropout(0.4),
    tf.keras.layers.Dense(32),
    keras.layers.Dropout(0.4),
    tf.keras.layers.Dense(16),
    keras.layers.Dropout(0.4),
    
    tf.keras.layers.Dense(1)
])

es_callback = keras.callbacks.EarlyStopping(monitor='loss', patience=8)

optimizer = tf.keras.optimizers.SGD(lr=0.001, momentum=0.9)

dense.compile(loss=tf.keras.losses.Huber(),
              optimizer=optimizer,
              metrics=["mae"])


RNN Model

In [ ]:
rnn = tf.keras.models.Sequential([
    tf.keras.layers.Lambda(lambda x: tf.expand_dims(x, axis=-1),
                      input_shape=[None]),
    tf.keras.layers.SimpleRNN(8, return_sequences=True),
    keras.layers.Dropout(0.4),
    
    tf.keras.layers.SimpleRNN(4),
    keras.layers.Dropout(0.4),
    
    tf.keras.layers.Dense(1),
    tf.keras.layers.Lambda(lambda x: x * 100.0)
])

es_callback = keras.callbacks.EarlyStopping(monitor='loss', patience=15)

optimizer = tf.keras.optimizers.SGD(lr=0.001, momentum=0.9)

rnn.compile(loss=tf.keras.losses.Huber(),
              optimizer=optimizer,
              metrics=["mae"])


GRU Model

In [ ]:
gru = tf.keras.models.Sequential([
    tf.keras.layers.Lambda(lambda x: tf.expand_dims(x, axis=-1),
                      input_shape=[None]),
    
    tf.keras.layers.GRU(32, return_sequences=True),
    keras.layers.Dropout(0.4),
    
    tf.keras.layers.GRU(32),
    keras.layers.Dropout(0.4),
    
    tf.keras.layers.Dense(1),
    tf.keras.layers.Lambda(lambda x: x * 100.0)
])

es_callback = keras.callbacks.EarlyStopping(monitor='loss', patience=6)

optimizer = tf.keras.optimizers.SGD(lr=0.001, momentum=0.9)

gru.compile(loss=tf.keras.losses.Huber(),
    optimizer=optimizer,
    metrics=["mae"])


LSTM Model

In [ ]:
lstm = tf.keras.models.Sequential([
    tf.keras.layers.Lambda(lambda x: tf.expand_dims(x, axis=-1),
                      input_shape=[None]),
    tf.keras.layers.Conv1D(filters=32, kernel_size=5,
                      strides=1, padding="causal",
                      activation="relu",
                      input_shape=[None, 1]),
    keras.layers.Dropout(0.4),
    
    tf.keras.layers.LSTM(32, return_sequences=True),
    keras.layers.Dropout(0.4),
    
    tf.keras.layers.LSTM(32),
    keras.layers.Dropout(0.4),
    
    tf.keras.layers.Dense(1),
    tf.keras.layers.Lambda(lambda x: x * 100.0)
])

es_callback = keras.callbacks.EarlyStopping(monitor='loss', patience=12)

optimizer = tf.keras.optimizers.SGD(lr=0.001, momentum=0.9)

lstm.compile(loss=tf.keras.losses.Huber(),
    optimizer=optimizer,
    metrics=["mae"])

Conv GRU Model

In [ ]:
conv_gru = tf.keras.models.Sequential([
    tf.keras.layers.Lambda(lambda x: tf.expand_dims(x, axis=-1),
                      input_shape=[None]),
    
    tf.keras.layers.Conv1D(filters=32, kernel_size=5,
                      strides=1, padding="causal",
                      activation="relu",
                      input_shape=[None, 1]),
    keras.layers.Dropout(0.4),
    
    tf.keras.layers.GRU(32, return_sequences=True),
    keras.layers.Dropout(0.4),
    
    tf.keras.layers.GRU(32),
    keras.layers.Dropout(0.4),
    tf.keras.layers.Dense(14),
    tf.keras.layers.Dense(1),
    tf.keras.layers.Lambda(lambda x: x * 100.0)
])

es_callback = keras.callbacks.EarlyStopping(monitor='loss', patience=10)

optimizer = tf.keras.optimizers.SGD(lr=0.001, momentum=0.9)

conv_gru.compile(loss=tf.keras.losses.Huber(),
    optimizer=optimizer,
    metrics=["mae"])

## Actual Daily Test

In [ ]:
# fix random seed for reproducibility
np.random.seed(8)
# load the dataset
dataframe = pd.read_csv('Data/RestaurantDataVets_All_2to5.csv')
data = dataframe.drop(columns=['Index','Group','DMY','MissingPrevDays'])

lookback=14
dataframe_removed_lookback = data.drop([x for x in range(lookback)])

for i in range(lookback):
    dataframe_removed_lookback[i] = 1.0
    
df = dataframe_removed_lookback[['Year', 'Day', 'January','February',
                         'March','April','May','June','July',
                         'August', 'September', 'October', 'November',
                         'December','Sunday', 'Monday', 'Tuesday',
                         'Wednesday', 'Thursday', 'Friday', 'Saturday', 'Holiday', 'Carnival', 
                         'LentFasting','Ramadan','ChristmasSeason',
                         0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13,
                         'DailyAvg','WeeklyAvg','MinSales','MaxSales','DailyBusyness',
                         'WeeklyBusyness','2to5']]
df = df.reset_index(drop=True)

#Objects need to be converted to float due to missing values at load time.
df["DailyAvg"] = df.DailyAvg.astype(float)
df["WeeklyAvg"] = df.WeeklyAvg.astype(float)
df["MinSales"] = df.MinSales.astype(float)
df["MaxSales"] = df.MaxSales.astype(float)
df["DailyBusyness"] = df.MaxSales.astype(float)
df["WeeklyBusyness"] = df.MaxSales.astype(float)

lb_data = add_lookback(data, lookback, df)
lb_data = lb_data.reset_index(drop=True)
hotdata = onehotholiday(lb_data)

numcols = len(hotdata.columns)
dataset = hotdata.values

print("train_df Shape:" ,lb_data.shape)
print("After encoding:", hotdata.shape)

X=dataset[:, 0:numcols-1]
y=dataset[:, numcols-1]

scaler = preprocessing.RobustScaler()
X = scaler.fit_transform(X,y)


In [ ]:
from sklearn.feature_selection import SelectPercentile, f_regression, mutual_info_regression, SelectKBest
sys.stdout.flush()

clflist=[dense, rnn, lstm, gru, conv_gru]  

recording = pd.DataFrame(clflist,columns=['Model'])



j_arr = []
for j in range (73):
    print('Keeping k-best features where k = ', (j+1))
    mae_arr = []
    loss_arr = []

    for x in range(len(clflist)):
        loss_arr.append(0)
        mae_arr.append(0)

    i=0
    for clf in clflist:

        reducer = SelectKBest(f_regression, k=(j+1))
        X_new=reducer.fit_transform(X,y)
        hist = clf.fit(X_new, y, epochs=100, callbacks=[es_callback])
                    
        loss_arr[i] = hist.history['loss'][-1]
        mae_arr[i] =  hist.history['mae'][-1]
            
        i= i+1
        print('_______________________________________________________________________________')
        
    j_arr.append(j+1)
    recording['Run'+str(j)] = mae_arr

print("COMPLETE")

In [ ]:
recording

In [ ]:
recording.to_csv('KerasResultsActual020121.csv')

## Daily Difference test - best features

In [ ]:
# fix random seed for reproducibility
np.random.seed(8)
# load the dataset
dataframe = pd.read_csv('Data/RestaurantDataVets_All_2to5_Differenced.csv')
data = dataframe.drop(columns=['Index','Group','DMY','MissingPrevDays', 'WeeklyDifference','DiffDifference','2to5'])

lookback=14
dataframe_removed_lookback = data.drop([x for x in range(lookback)])
for i in range(lookback):
    dataframe_removed_lookback[i] = 1.0


df = dataframe_removed_lookback[['Year', 'Day', 'January','February',
                         'March','April','May','June','July',
                         'August', 'September', 'October', 'November',
                         'December','Sunday', 'Monday', 'Tuesday',
                         'Wednesday', 'Thursday', 'Friday', 'Saturday', 'Holiday', 'Carnival', 
                         'LentFasting','Ramadan','ChristmasSeason', 0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 
                         'DailyAvg','WeeklyAvg','MinSales','MaxSales','DailyBusyness',
                          'WeeklyBusyness','AvgDailyDiff','AvgWeeklyDiff','MinDailyDiff',
                         'MaxDailyDiff', 
                        'DailyDifference']]

df = df.reset_index(drop=True)

#Objects need to be converted to float due to missing values at load time.
df["DailyAvg"] = df.DailyAvg.astype(float)
df["WeeklyAvg"] = df.WeeklyAvg.astype(float)
df["MinSales"] = df.MinSales.astype(float)
df["MaxSales"] = df.MaxSales.astype(float)
df["DailyBusyness"] = df.DailyBusyness.astype(float)
df["WeeklyBusyness"] = df.WeeklyBusyness.astype(float)


df["AvgDailyDiff"] = df.AvgDailyDiff.astype(float)
df["AvgWeeklyDiff"] = df.AvgWeeklyDiff.astype(float)
df["MaxDailyDiff"] = df.MaxDailyDiff.astype(float)
df["MinDailyDiff"] = df.MinDailyDiff.astype(float)
df["DailyDifference"] = df.DailyDifference.astype(float)

diff_add_lookback(data, lookback, df,'DailyDifference')
#lb_data = lb_data.reset_index(drop=True)
hotdata = onehotholidaydiff(df,'DailyDifference')

hotdata = hotdata.drop([x for x in range(7)])
hotdata = hotdata.reset_index(drop=True)

cols = hotdata.columns[hotdata.dtypes.eq('object')]
hotdata[cols] = hotdata[cols].apply(pd.to_numeric, errors='coerce', axis=1)

numcols = len(hotdata.columns)
dataset = hotdata.values

print("train_df Shape:" ,data.shape)
print("After encoding:", hotdata.shape)


In [ ]:
hotdata

In [ ]:
from sklearn.feature_selection import SelectPercentile, f_regression, mutual_info_regression, SelectKBest
sys.stdout.flush()

X=dataset[:, 0:numcols-1]
y=dataset[:, numcols-1]

clflist=[dense, rnn, lstm, gru, conv_gru]  

recording = pd.DataFrame(clflist,columns=['Model'])



j_arr = []
for j in range (77):
    print('Keeping k-best features where k = ', (j+1))
    mae_arr = []
    loss_arr = []

    for x in range(len(clflist)):
        loss_arr.append(0)
        mae_arr.append(0)

    i=0
    for clf in clflist:

        reducer = SelectKBest(f_regression, k=(j+1))
        X_new=reducer.fit_transform(X,y)
        hist = clf.fit(X_new, y, epochs=100, callbacks=[es_callback])
                    
        loss_arr[i] = hist.history['loss'][-1]
        mae_arr[i] =  hist.history['mae'][-1]
            
        i= i+1
        print('_______________________________________________________________________________')
        
    j_arr.append(j+1)
    recording['Run'+str(j)] = mae_arr

print("COMPLETE")

In [ ]:
recording

In [ ]:
recording.to_csv('KerasResultsDailyDiff02012021.csv')

## Weekly Difference Test - best features

In [ ]:
# fix random seed for reproducibility
np.random.seed(8)
# load the dataset
dataframe = pd.read_csv('Data/RestaurantDataVets_All_2to5_Differenced.csv')
data = dataframe.drop(columns=['Index','Group','DMY','MissingPrevDays', 'DailyDifference','DiffDifference','2to5'])

lookback=14
dataframe_removed_lookback = data.drop([x for x in range(lookback)])
for i in range(lookback):
    dataframe_removed_lookback[i] = 1.0


df = dataframe_removed_lookback[['Year', 'Day', 'January','February',
                         'March','April','May','June','July',
                         'August', 'September', 'October', 'November',
                         'December','Sunday', 'Monday', 'Tuesday',
                         'Wednesday', 'Thursday', 'Friday', 'Saturday', 'Holiday', 'Carnival', 
                         'LentFasting','Ramadan','ChristmasSeason', 0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 
                         'DailyAvg','WeeklyAvg','MinSales','MaxSales','DailyBusyness',
                          'WeeklyBusyness','AvgDailyDiff','AvgWeeklyDiff','MinDailyDiff',
                         'MaxDailyDiff', 
                        'WeeklyDifference']]

df = df.reset_index(drop=True)

#Objects need to be converted to float due to missing values at load time.
df["DailyAvg"] = df.DailyAvg.astype(float)
df["WeeklyAvg"] = df.WeeklyAvg.astype(float)
df["MinSales"] = df.MinSales.astype(float)
df["MaxSales"] = df.MaxSales.astype(float)
df["DailyBusyness"] = df.DailyBusyness.astype(float)
df["WeeklyBusyness"] = df.WeeklyBusyness.astype(float)


df["AvgDailyDiff"] = df.AvgDailyDiff.astype(float)
df["AvgWeeklyDiff"] = df.AvgWeeklyDiff.astype(float)
df["MaxDailyDiff"] = df.MaxDailyDiff.astype(float)
df["MinDailyDiff"] = df.MinDailyDiff.astype(float)
df["WeeklyDifference"] = df.WeeklyDifference.astype(float)

diff_add_lookback(data, lookback, df,'WeeklyDifference')
#lb_data = lb_data.reset_index(drop=True)
hotdata = onehotholidaydiff(df,'WeeklyDifference')

hotdata = hotdata.drop([x for x in range(7)])
hotdata = hotdata.reset_index(drop=True)

cols = hotdata.columns[hotdata.dtypes.eq('object')]
hotdata[cols] = hotdata[cols].apply(pd.to_numeric, errors='coerce', axis=1)

numcols = len(hotdata.columns)
dataset = hotdata.values

print("train_df Shape:" ,data.shape)
print("After encoding:", hotdata.shape)



In [ ]:
hotdata

In [ ]:
from sklearn.feature_selection import SelectPercentile, f_regression, mutual_info_regression, SelectKBest
sys.stdout.flush()

X=dataset[:, 0:numcols-1]
y=dataset[:, numcols-1]

clflist=[dense, rnn, gru, lstm, conv_gru]  

recording = pd.DataFrame(clflist,columns=['Model'])



j_arr = []
for j in range (77):
    print('Keeping k-best features where k = ', (j+1))
    mae_arr = []
    loss_arr = []

    for x in range(len(clflist)):
        loss_arr.append(0)
        mae_arr.append(0)

    i=0
    for clf in clflist:

        reducer = SelectKBest(f_regression, k=(j+1))
        X_new=reducer.fit_transform(X,y)
        hist = clf.fit(X_new, y, epochs=100, callbacks=[es_callback])
                    
        loss_arr[i] = hist.history['loss'][-1]
        mae_arr[i] =  hist.history['mae'][-1]
            
        i= i+1
        print('_______________________________________________________________________________')
        
    j_arr.append(j+1)
    recording['Run'+str(j)] = mae_arr

print("COMPLETE")

In [ ]:
recording

In [ ]:
recording.to_csv('KerasResultsWeeklyDiff02012021.csv')

# One Week Forecast

In [3]:
dense = tf.keras.models.Sequential([
    tf.keras.layers.Lambda(lambda x: tf.expand_dims(x, axis=-1),
                      input_shape=[None]),
    tf.keras.layers.Dense(64),
    keras.layers.Dropout(0.4),
    tf.keras.layers.Dense(32),
    keras.layers.Dropout(0.4),
    tf.keras.layers.Dense(16),
    keras.layers.Dropout(0.4),
    
    tf.keras.layers.Dense(7)
])

es_callback = keras.callbacks.EarlyStopping(monitor='loss', patience=8)

optimizer = tf.keras.optimizers.SGD(lr=0.001, momentum=0.9)

dense.compile(loss=tf.keras.losses.Huber(),
              optimizer=optimizer,
              metrics=["mae"])

In [4]:
rnn = tf.keras.models.Sequential([
    tf.keras.layers.Lambda(lambda x: tf.expand_dims(x, axis=-1),
                      input_shape=[None]),
    tf.keras.layers.SimpleRNN(8, return_sequences=True),
    keras.layers.Dropout(0.4),
    
    tf.keras.layers.SimpleRNN(4),
    keras.layers.Dropout(0.4),
    
    tf.keras.layers.Dense(7),
    tf.keras.layers.Lambda(lambda x: x * 100.0)
])

es_callback = keras.callbacks.EarlyStopping(monitor='loss', patience=15)

optimizer = tf.keras.optimizers.SGD(lr=0.001, momentum=0.9)

rnn.compile(loss=tf.keras.losses.Huber(),
              optimizer=optimizer,
              metrics=["mae"])


In [5]:
gru = tf.keras.models.Sequential([
    tf.keras.layers.Lambda(lambda x: tf.expand_dims(x, axis=-1),
                      input_shape=[None]),
    
    tf.keras.layers.GRU(32, return_sequences=True),
    keras.layers.Dropout(0.4),
    
    tf.keras.layers.GRU(32),
    keras.layers.Dropout(0.4),
    
    tf.keras.layers.Dense(7),
    tf.keras.layers.Lambda(lambda x: x * 100.0)
])

es_callback = keras.callbacks.EarlyStopping(monitor='loss', patience=6)

optimizer = tf.keras.optimizers.SGD(lr=0.001, momentum=0.9)

gru.compile(loss=tf.keras.losses.Huber(),
    optimizer=optimizer,
    metrics=["mae"])


In [6]:
lstm = tf.keras.models.Sequential([
    tf.keras.layers.Lambda(lambda x: tf.expand_dims(x, axis=-1),
                      input_shape=[None]),
    tf.keras.layers.Conv1D(filters=32, kernel_size=5,
                      strides=1, padding="causal",
                      activation="relu",
                      input_shape=[None, 1]),
    keras.layers.Dropout(0.4),
    
    tf.keras.layers.LSTM(32, return_sequences=True),
    keras.layers.Dropout(0.4),
    
    tf.keras.layers.LSTM(32),
    keras.layers.Dropout(0.4),
    
    tf.keras.layers.Dense(7),
    tf.keras.layers.Lambda(lambda x: x * 100.0)
])

es_callback = keras.callbacks.EarlyStopping(monitor='loss', patience=12)

optimizer = tf.keras.optimizers.SGD(lr=0.001, momentum=0.9)

lstm.compile(loss=tf.keras.losses.Huber(),
    optimizer=optimizer,
    metrics=["mae"])

In [7]:
conv_gru = tf.keras.models.Sequential([
    tf.keras.layers.Lambda(lambda x: tf.expand_dims(x, axis=-1),
                      input_shape=[None]),
    
    tf.keras.layers.Conv1D(filters=32, kernel_size=5,
                      strides=1, padding="causal",
                      activation="relu",
                      input_shape=[None, 1]),
    keras.layers.Dropout(0.4),
    
    tf.keras.layers.GRU(32, return_sequences=True),
    keras.layers.Dropout(0.4),
    
    tf.keras.layers.GRU(32),
    keras.layers.Dropout(0.4),
    tf.keras.layers.Dense(14),
    tf.keras.layers.Dense(7),
    tf.keras.layers.Lambda(lambda x: x * 100.0)
])

es_callback = keras.callbacks.EarlyStopping(monitor='loss', patience=10)

optimizer = tf.keras.optimizers.SGD(lr=0.001, momentum=0.9)

conv_gru.compile(loss=tf.keras.losses.Huber(),
    optimizer=optimizer,
    metrics=["mae"])

## Actual

In [ ]:
np.random.seed(42)
# fix random seed for reproducibility
# load the dataset
dataframe = pd.read_csv('Data/RestaurantDataVets_All_2to5.csv')
data = dataframe.drop(columns=['Index','Group','DMY','MissingPrevDays','DailyAvg','DailyBusyness'])

lookback=20
dataframe_removed_lookback = data.drop([x for x in range(lookback)])

for i in range(lookback):
    dataframe_removed_lookback[i] = 1.0
    
df = dataframe_removed_lookback[['Year', 'Day', 'January','February',
                         'March','April','May','June','July',
                         'August', 'September', 'October', 'November',
                         'December','Sunday', 'Monday', 'Tuesday',
                         'Wednesday', 'Thursday', 'Friday', 'Saturday', 'Holiday', 'Carnival', 
                         'LentFasting','Ramadan','ChristmasSeason',
                         'WeeklyAvg','MinSales','MaxSales',
                         'WeeklyBusyness',
                         0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13,
                          14, 15, 16, 17, 18, 19,      
                         '2to5']]
df = df.reset_index(drop=True)

#Objects need to be converted to float due to missing values at load time.
#df["DailyAvg"] = df.DailyAvg.astype(float)
df["WeeklyAvg"] = df.WeeklyAvg.astype(float)
df["MinSales"] = df.MinSales.astype(float)
df["MaxSales"] = df.MaxSales.astype(float)
#df["DailyBusyness"] = df.DailyBusyness.astype(float)
df["WeeklyBusyness"] = df.WeeklyBusyness.astype(float)

lb_data = add_lookback(data, lookback, df)
lb_data = lb_data.reset_index(drop=True)

hotdata = onehotholiday(lb_data)
hotdata = hotdata.drop(columns=[14,15,16,17,18,19])

hot_numcols = len(hotdata.columns)
dataset = hotdata.values

lbset=lb_data.values
lb_numcols =  len(lb_data.columns)

print("train_df Shape:" ,lb_data.shape)
print("After encoding:", hotdata.shape)

In [ ]:
X=dataset[:, 0:hot_numcols-1]
y=lbset[:, lb_numcols-7:lb_numcols]

scaler = preprocessing.RobustScaler()
X = scaler.fit_transform(X,y)

sys.stdout.flush()

clflist=[rnn, lstm, gru, conv_gru]   
recording = pd.DataFrame(clflist,columns=['Model'])

 

week_actual_recording = pd.DataFrame(clflist,columns=['Model'])



j_arr = []
for j in range (72):
    print('Keeping k-best features where k = ', (j+1))
    mae_arr = []
    loss_arr = []

    for x in range(len(clflist)):
        loss_arr.append(0)
        mae_arr.append(0)

    i=0
    for clf in clflist:

        reducer = SelectKBest(f_regression, k=(j+1))
        X_new=reducer.fit_transform(X,y[:,0])
        hist = clf.fit(X_new, y, epochs=100, callbacks=[es_callback])
                    
        loss_arr[i] = hist.history['loss'][-1]
        mae_arr[i] =  hist.history['mae'][-1]
            
        i= i+1
        print('_______________________________________________________________________________')
        
    j_arr.append(j+1)
    week_actual_recording['Run'+str(j)] = mae_arr

print("COMPLETE")

In [ ]:
week_actual_recording

In [ ]:
week_actual_recording.to_csv('KerasResultsWeekActual02012021.csv')

## Daily Difference

In [ ]:
np.random.seed(42)
# fix random seed for reproducibility
# load the dataset
dataframe = pd.read_csv('Data/RestaurantDataVets_All_2to5_Differenced.csv')
data = dataframe.drop(columns=['Index','Group','DMY','MissingPrevDays','WeeklyDifference','DailyAvg',
                               'DailyBusyness','AvgDailyDiff','DiffDifference','2to5'])
remove=1
data = data.drop([x for x in range(remove)])
data = data.reset_index(drop=True)
lookback=20
dataframe_removed_lookback = data.drop([x for x in range(lookback)])

for i in range(lookback):
    dataframe_removed_lookback[i] = 1.0
    
df = dataframe_removed_lookback[['Year', 'Day', 'January','February',
                         'March','April','May','June','July',
                         'August', 'September', 'October', 'November',
                         'December','Sunday', 'Monday', 'Tuesday',
                         'Wednesday', 'Thursday', 'Friday', 'Saturday', 'Holiday', 'Carnival', 
                         'LentFasting','Ramadan','ChristmasSeason','WeeklyAvg','MinSales','MaxSales',
                          'WeeklyBusyness','AvgWeeklyDiff','MinDailyDiff',
                         'MaxDailyDiff',
                                 0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13,
                                 14, 15, 16, 17, 18, 19,  
                        'DailyDifference']]
df = df.reset_index(drop=True)

#Objects need to be converted to float due to missing values at load time.
#df["DailyAvg"] = df.DailyAvg.astype(float)
df["WeeklyAvg"] = df.WeeklyAvg.astype(float)
df["MinSales"] = df.MinSales.astype(float)
df["MaxSales"] = df.MaxSales.astype(float)
#df["DailyBusyness"] = df.DailyBusyness.astype(float)
df["WeeklyBusyness"] = df.WeeklyBusyness.astype(float)

#df["AvgDailyDiff"] = df.AvgDailyDiff.astype(float)
df["AvgWeeklyDiff"] = df.AvgWeeklyDiff.astype(float)
df["MaxDailyDiff"] = df.MaxDailyDiff.astype(float)
df["MinDailyDiff"] = df.MinDailyDiff.astype(float)
df["DailyDifference"] = df.DailyDifference.astype(float)
#df["WeeklyDifference"] = df.WeeklyDifference.astype(float

lb_data = diff_add_lookback(data, lookback, df,'DailyDifference')
lb_data = lb_data.reset_index(drop=True)

hotdata = onehotholidaydiff(lb_data, 'DailyDifference')
hotdata = hotdata.drop(columns=[14,15,16,17,18,19])


hot_numcols = len(hotdata.columns)
dataset = hotdata.values

lbset=lb_data.values
lb_numcols =  len(lb_data.columns)

print("train_df Shape:" ,lb_data.shape)
print("After encoding:", hotdata.shape)

In [ ]:
hotdata

In [ ]:
X=dataset[:, 0:hot_numcols-1]
y=lbset[:, lb_numcols-7:lb_numcols]

scaler = preprocessing.RobustScaler()
X = scaler.fit_transform(X,y)

sys.stdout.flush()

clflist=[rnn, lstm, gru, conv_gru]   
recording = pd.DataFrame(clflist,columns=['Model'])

 

week_daydiff_recording = pd.DataFrame(clflist,columns=['Model'])



j_arr = []
for j in range (74):
    print('Keeping k-best features where k = ', (j+1))
    mae_arr = []
    loss_arr = []

    for x in range(len(clflist)):
        loss_arr.append(0)
        mae_arr.append(0)

    i=0
    for clf in clflist:

        reducer = SelectKBest(f_regression, k=(j+1))
        X_new=reducer.fit_transform(X,y[:,0])
        hist = clf.fit(X_new, y, epochs=100, callbacks=[es_callback])
                    
        loss_arr[i] = hist.history['loss'][-1]
        mae_arr[i] =  hist.history['mae'][-1]
            
        i= i+1
        print('_______________________________________________________________________________')
        
    j_arr.append(j+1)
    week_daydiff_recording['Run'+str(j)] = mae_arr

print("COMPLETE")

In [ ]:
week_daydiff_recording

In [ ]:
week_daydiff_recording.to_csv('KerasResultsWeekDayDiff02012021.csv')

## Weekly Difference

In [8]:
np.random.seed(42)
# fix random seed for reproducibility
# load the dataset
dataframe = pd.read_csv('Data/RestaurantDataVets_All_2to5_Differenced.csv')
data = dataframe.drop(columns=['Index','Group','DMY','MissingPrevDays','DailyDifference',
                               'DailyAvg','DailyBusyness','AvgDailyDiff','DiffDifference','2to5'])
remove=7
data = data.drop([x for x in range(remove)])
data = data.reset_index(drop=True)
lookback=20
dataframe_removed_lookback = data.drop([x for x in range(lookback)])

for i in range(lookback):
    dataframe_removed_lookback[i] = 1.0
    
df = dataframe_removed_lookback[['Year', 'Day', 'January','February',
                         'March','April','May','June','July',
                         'August', 'September', 'October', 'November',
                         'December','Sunday', 'Monday', 'Tuesday',
                         'Wednesday', 'Thursday', 'Friday', 'Saturday', 'Holiday', 'Carnival', 
                         'LentFasting','Ramadan','ChristmasSeason','WeeklyAvg','MinSales','MaxSales',
                          'WeeklyBusyness','AvgWeeklyDiff','MinDailyDiff',
                         'MaxDailyDiff',
                                 0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13,
                                 14, 15, 16, 17, 18, 19,  
                        'WeeklyDifference']]
df = df.reset_index(drop=True)

#Objects need to be converted to float due to missing values at load time.
#df["DailyAvg"] = df.DailyAvg.astype(float)
df["WeeklyAvg"] = df.WeeklyAvg.astype(float)
df["MinSales"] = df.MinSales.astype(float)
df["MaxSales"] = df.MaxSales.astype(float)
#df["DailyBusyness"] = df.DailyBusyness.astype(float)
df["WeeklyBusyness"] = df.WeeklyBusyness.astype(float)

#df["AvgDailyDiff"] = df.AvgDailyDiff.astype(float)
df["AvgWeeklyDiff"] = df.AvgWeeklyDiff.astype(float)
df["MaxDailyDiff"] = df.MaxDailyDiff.astype(float)
df["MinDailyDiff"] = df.MinDailyDiff.astype(float)
#df["DailyDifference"] = df.DailyDifference.astype(float)
df["WeeklyDifference"] = df.WeeklyDifference.astype(float)

lb_data = diff_add_lookback(data, lookback, df,'WeeklyDifference')
lb_data = lb_data.reset_index(drop=True)

hotdata = onehotholidaydiff(lb_data, 'WeeklyDifference')
hotdata = hotdata.drop(columns=[14,15,16,17,18,19])

hot_numcols = len(hotdata.columns)
dataset = hotdata.values

lbset=lb_data.values
lb_numcols =  len(lb_data.columns)

print("train_df Shape:" ,lb_data.shape)
print("After encoding:", hotdata.shape)


train_df Shape: (1084, 54)
After encoding: (1084, 75)


In [9]:
hotdata

Year  Day  January  February  March  April  May  June  July  August  \
0     2016    8        0         0      0      0    0     0     0       0   
1     2016    9        0         0      0      0    0     0     0       0   
2     2016   10        0         0      0      0    0     0     0       0   
3     2016   11        0         0      0      0    0     0     0       0   
4     2016   12        0         0      0      0    0     0     0       0   
...    ...  ...      ...       ...    ...    ...  ...   ...   ...     ...   
1079  2019    1        0         0      0      0    0     0     0       0   
1080  2019    2        0         0      0      0    0     0     0       0   
1081  2019    3        0         0      0      0    0     0     0       0   
1082  2019    4        0         0      0      0    0     0     0       0   
1083  2019    5        0         0      0      0    0     0     0       0   

      September  October  November  December  Sunday  Monday  Tuesday  \
0             0        1         0         0       0       0        0   
1             0        1         0         0       1       0        0   
2             0        1         0         0       0       1        0   
3             0        1         0         0       0       0        1   
4             0        1         0         0       0       0        0   
...         ...      ...       ...       ...     ...     ...      ...   
1079          0        0         0         1       1       0        0   
1080          0        0         0         1       0       1        0   
1081          0        0         0         1       0       0        1   
1082          0        0         0         1       0       0        0   
1083          0        0         0         1       0       0        0   

      Wednesday  Thursday  Friday  Saturday  Carnival  LentFasting  Ramadan  \
0             0         0       0         1         0            0        0   
1             0         0       0         0         0            0        0   
2             0         0       0         0         0            0        0   
3             0         0       0         0         0            0        0   
4             1         0       0         0         0            0        0   
...         ...       ...     ...       ...       ...          ...      ...   
1079          0         0       0         0         0            0        0   
1080          0         0       0         0         0            0        0   
1081          0         0       0         0         0            0        0   
1082          1         0       0         0         0            0        0   
1083          0         1       0         0         0            0        0   

      ChristmasSeason  WeeklyAvg  MinSales  MaxSales  WeeklyBusyness  \
0                   0   915.4533  318.7400 1060.1100          0.8049   
1                   0   795.1350  318.7400 1060.1100          0.6426   
2                   0   432.3950  318.7400 1060.1100          0.1533   
3                   0   379.3025  318.7400 1060.1100          0.0817   
4                   0   386.8400  318.7400 1060.1100          0.0919   
...               ...        ...       ...       ...             ...   
1079                1  1445.3206  225.3000 2889.2300          0.4580   
1080                1   809.8104  225.3000 2889.2300          0.2194   
1081                1   769.9493  225.3000 2889.2300          0.2044   
1082                1   839.7848  225.3000 2889.2300          0.2307   
1083                1   827.5773  225.3000 2889.2300          0.2261   

      AvgWeeklyDiff  MinDailyDiff  MaxDailyDiff         0         1         2  \
0           99.0350     -515.3900      494.1200  276.4900  -47.9400   57.8200   
1            6.7333     -515.3900      494.1200  -47.9400   57.8200   55.3700   
2          -15.4800     -515.3900      494.1200   57.8200   55.3700   46.1700   
3           -0.6000     -515.3900      494.1200   55.3700   46.170

In [10]:
X=dataset[:, 0:hot_numcols-1]
y=lbset[:, lb_numcols-7:lb_numcols]

scaler = preprocessing.RobustScaler()
X = scaler.fit_transform(X,y)

sys.stdout.flush()

clflist=[rnn, lstm, gru, conv_gru]   
recording = pd.DataFrame(clflist,columns=['Model'])

 

week_weekdiff_recording= pd.DataFrame(clflist,columns=['Model'])



j_arr = []
for j in range (74):
    print('Keeping k-best features where k = ', (j+1))
    mae_arr = []
    loss_arr = []

    for x in range(len(clflist)):
        loss_arr.append(0)
        mae_arr.append(0)

    i=0
    for clf in clflist:

        reducer = SelectKBest(f_regression, k=(j+1))
        X_new=reducer.fit_transform(X,y[:,0])
        hist = clf.fit(X_new, y, epochs=100, callbacks=[es_callback])
                    
        loss_arr[i] = hist.history['loss'][-1]
        mae_arr[i] =  hist.history['mae'][-1]
            
        i= i+1
        print('_______________________________________________________________________________')
        
    j_arr.append(j+1)
    week_weekdiff_recording['Run'+str(j)] = mae_arr

print("COMPLETE")

Keeping k-best features where k =  1
Epoch 1/100
34/34 [==============================] - ETA: 0s - loss: 241.9321 - mae: 242.432 - 0s 1ms/step - loss: 250.4399 - mae: 250.9393
Epoch 2/100
34/34 [==============================] - ETA: 0s - loss: 244.1943 - mae: 244.694 - 0s 1ms/step - loss: 250.1049 - mae: 250.6043
Epoch 3/100
34/34 [==============================] - ETA: 0s - loss: 239.6518 - mae: 240.151 - 0s 1ms/step - loss: 249.2406 - mae: 249.7401
Epoch 4/100
34/34 [==============================] - ETA: 0s - loss: 262.0888 - mae: 262.588 - 0s 1ms/step - loss: 248.9671 - mae: 249.4666
Epoch 5/100
34/34 [==============================] - ETA: 0s - loss: 262.4794 - mae: 262.979 - 0s 1ms/step - loss: 249.1239 - mae: 249.6232
Epoch 6/100
34/34 [==============================] - ETA: 0s - loss: 291.6115 - mae: 292.111 - 0s 1ms/step - loss: 249.2337 - mae: 249.7332
Epoch 7/100
34/34 [==============================] - ETA: 0s - loss: 259.4304 - mae: 259.929 - 0s 1ms/step - loss: 249.3378

Epoch 62/100
34/34 [==============================] - ETA: 0s - loss: 254.7687 - mae: 255.265 - ETA: 0s - loss: 248.5360 - mae: 249.035 - 0s 3ms/step - loss: 247.8449 - mae: 248.3440
Epoch 63/100
34/34 [==============================] - ETA: 0s - loss: 241.8578 - mae: 242.357 - ETA: 0s - loss: 253.3427 - mae: 253.842 - 0s 3ms/step - loss: 248.2411 - mae: 248.7406
Epoch 64/100
34/34 [==============================] - ETA: 0s - loss: 236.2051 - mae: 236.705 - ETA: 0s - loss: 247.1526 - mae: 247.652 - 0s 3ms/step - loss: 247.8010 - mae: 248.3004
Epoch 65/100
34/34 [==============================] - ETA: 0s - loss: 214.9450 - mae: 215.444 - ETA: 0s - loss: 250.9502 - mae: 251.449 - 0s 3ms/step - loss: 247.8505 - mae: 248.3499
Epoch 66/100
34/34 [==============================] - ETA: 0s - loss: 258.5024 - mae: 259.002 - ETA: 0s - loss: 248.4797 - mae: 248.979 - 0s 3ms/step - loss: 248.5082 - mae: 249.0077
Epoch 67/100
34/34 [==============================] - ETA: 0s - loss: 253.4266 - mae:

_______________________________________________________________________________
Keeping k-best features where k =  2
Epoch 1/100
34/34 [==============================] - ETA: 0s - loss: 228.3435 - mae: 228.843 - ETA: 0s - loss: 250.5595 - mae: 251.059 - 0s 2ms/step - loss: 250.1584 - mae: 250.6579
Epoch 2/100
34/34 [==============================] - ETA: 0s - loss: 246.8101 - mae: 247.309 - ETA: 0s - loss: 249.5341 - mae: 250.033 - 0s 2ms/step - loss: 248.4960 - mae: 248.9951
Epoch 3/100
34/34 [==============================] - ETA: 0s - loss: 260.1271 - mae: 260.626 - ETA: 0s - loss: 250.2455 - mae: 250.744 - 0s 2ms/step - loss: 248.7480 - mae: 249.2471
Epoch 4/100
34/34 [==============================] - ETA: 0s - loss: 228.0370 - mae: 228.536 - ETA: 0s - loss: 247.8884 - mae: 248.388 - 0s 2ms/step - loss: 248.4798 - mae: 248.9794
Epoch 5/100
34/34 [==============================] - ETA: 0s - loss: 286.7866 - mae: 287.285 - ETA: 0s - loss: 249.6174 - mae: 250.116 - 0s 2ms/step - loss

34/34 [==============================] - ETA: 0s - loss: 258.1639 - mae: 258.662 - ETA: 0s - loss: 245.7242 - mae: 246.223 - ETA: 0s - loss: 247.1504 - mae: 247.649 - 0s 4ms/step - loss: 247.8651 - mae: 248.3646
Epoch 14/100
34/34 [==============================] - ETA: 0s - loss: 250.7871 - mae: 251.286 - ETA: 0s - loss: 248.0623 - mae: 248.561 - ETA: 0s - loss: 247.4293 - mae: 247.928 - 0s 4ms/step - loss: 248.0104 - mae: 248.5098
Epoch 15/100
34/34 [==============================] - ETA: 0s - loss: 221.0946 - mae: 221.594 - ETA: 0s - loss: 253.9711 - mae: 254.470 - ETA: 0s - loss: 248.3963 - mae: 248.895 - 0s 4ms/step - loss: 247.9391 - mae: 248.4387
Epoch 16/100
34/34 [==============================] - ETA: 0s - loss: 274.5428 - mae: 275.042 - ETA: 0s - loss: 242.9506 - mae: 243.450 - ETA: 0s - loss: 247.8846 - mae: 248.384 - 0s 3ms/step - loss: 248.0901 - mae: 248.5895
Epoch 17/100
34/34 [==============================] - ETA: 0s - loss: 212.7564 - mae: 213.256 - ETA: 0s - loss: 2

34/34 [==============================] - ETA: 0s - loss: 235.6377 - mae: 236.137 - ETA: 0s - loss: 244.3805 - mae: 244.879 - ETA: 0s - loss: 246.6228 - mae: 247.121 - 0s 4ms/step - loss: 246.8460 - mae: 247.3453
Epoch 29/100
34/34 [==============================] - ETA: 0s - loss: 242.9216 - mae: 243.420 - ETA: 0s - loss: 252.6627 - mae: 253.161 - ETA: 0s - loss: 247.9784 - mae: 248.477 - 0s 4ms/step - loss: 246.8698 - mae: 247.3689
Epoch 30/100
34/34 [==============================] - ETA: 0s - loss: 243.3206 - mae: 243.820 - ETA: 0s - loss: 248.1023 - mae: 248.601 - ETA: 0s - loss: 248.2322 - mae: 248.731 - 0s 4ms/step - loss: 246.3120 - mae: 246.8115
Epoch 31/100
34/34 [==============================] - ETA: 0s - loss: 235.2634 - mae: 235.762 - ETA: 0s - loss: 247.7792 - mae: 248.278 - ETA: 0s - loss: 247.5129 - mae: 248.012 - 0s 4ms/step - loss: 246.3962 - mae: 246.8959
Epoch 32/100
34/34 [==============================] - ETA: 0s - loss: 297.8017 - mae: 298.298 - ETA: 0s - loss: 2

...

34/34 [==============================] - ETA: 0s - loss: 228.9817 - mae: 229.481 - ETA: 0s - loss: 219.9895 - mae: 220.489 - ETA: 0s - loss: 218.0415 - mae: 218.541 - ETA: 0s - loss: 219.9509 - mae: 220.450 - ETA: 0s - loss: 216.6119 - mae: 217.111 - ETA: 0s - loss: 216.0130 - mae: 216.512 - ETA: 0s - loss: 214.8138 - mae: 215.313 - ETA: 0s - loss: 216.6683 - mae: 217.167 - ETA: 0s - loss: 214.2948 - mae: 214.794 - ETA: 0s - loss: 213.7141 - mae: 214.213 - ETA: 0s - loss: 213.7099 - mae: 214.209 - ETA: 0s - loss: 212.2360 - mae: 212.735 - ETA: 0s - loss: 214.5223 - mae: 215.021 - ETA: 0s - loss: 213.7590 - mae: 214.258 - ETA: 0s - loss: 212.2958 - mae: 212.795 - ETA: 0s - loss: 211.5427 - mae: 212.042 - ETA: 0s - loss: 212.3268 - mae: 212.826 - 1s 38ms/step - loss: 212.2355 - mae: 212.7348
Epoch 15/100
34/34 [==============================] - ETA: 0s - loss: 232.5825 - mae: 233.082 - ETA: 0s - loss: 218.8751 - mae: 219.375 - ETA: 0s - loss: 210.3855 - mae: 210.885 - ETA: 0s - loss: 213

Epoch 5/100
34/34 [==============================] - ETA: 0s - loss: 267.2306 - mae: 267.729 - ETA: 0s - loss: 260.3448 - mae: 260.844 - ETA: 0s - loss: 251.1532 - mae: 251.652 - ETA: 0s - loss: 249.7900 - mae: 250.289 - ETA: 0s - loss: 252.5534 - mae: 253.052 - ETA: 0s - loss: 252.8768 - mae: 253.376 - ETA: 0s - loss: 249.0803 - mae: 249.579 - ETA: 0s - loss: 247.5764 - mae: 248.075 - ETA: 0s - loss: 249.0013 - mae: 249.500 - ETA: 0s - loss: 250.0014 - mae: 250.500 - ETA: 0s - loss: 250.0741 - mae: 250.573 - ETA: 0s - loss: 248.9557 - mae: 249.455 - ETA: 0s - loss: 248.7633 - mae: 249.262 - ETA: 0s - loss: 248.5676 - mae: 249.066 - ETA: 0s - loss: 246.5848 - mae: 247.084 - ETA: 0s - loss: 245.6064 - mae: 246.105 - ETA: 0s - loss: 246.1941 - mae: 246.693 - 1s 40ms/step - loss: 247.2728 - mae: 247.7720
Epoch 6/100
34/34 [==============================] - ETA: 0s - loss: 241.4593 - mae: 241.957 - ETA: 0s - loss: 236.6669 - mae: 237.165 - ETA: 1s - loss: 238.3213 - mae: 238.820 - ETA: 0s 

34/34 [==============================] - ETA: 0s - loss: 262.1788 - mae: 262.678 - ETA: 0s - loss: 253.5087 - mae: 254.008 - ETA: 0s - loss: 256.1426 - mae: 256.642 - ETA: 0s - loss: 253.0921 - mae: 253.591 - ETA: 0s - loss: 256.1058 - mae: 256.605 - ETA: 0s - loss: 252.8780 - mae: 253.377 - ETA: 0s - loss: 251.5192 - mae: 252.018 - ETA: 0s - loss: 251.7143 - mae: 252.213 - ETA: 0s - loss: 252.5795 - mae: 253.078 - ETA: 0s - loss: 253.0211 - mae: 253.520 - ETA: 0s - loss: 250.1416 - mae: 250.641 - ETA: 0s - loss: 249.9070 - mae: 250.406 - ETA: 0s - loss: 249.6761 - mae: 250.175 - ETA: 0s - loss: 248.0925 - mae: 248.591 - ETA: 0s - loss: 247.8882 - mae: 248.387 - ETA: 0s - loss: 246.8509 - mae: 247.350 - ETA: 0s - loss: 246.9459 - mae: 247.445 - 1s 40ms/step - loss: 246.8739 - mae: 247.3733
Epoch 26/100
34/34 [==============================] - ETA: 0s - loss: 222.6249 - mae: 223.121 - ETA: 0s - loss: 226.6021 - mae: 227.099 - ETA: 0s - loss: 226.5623 - mae: 227.060 - ETA: 0s - loss: 228

34/34 [==============================] - ETA: 0s - loss: 261.9634 - mae: 262.461 - ETA: 0s - loss: 246.3305 - mae: 246.829 - ETA: 0s - loss: 245.1811 - mae: 245.680 - ETA: 0s - loss: 244.5752 - mae: 245.074 - ETA: 0s - loss: 244.0242 - mae: 244.523 - ETA: 0s - loss: 242.8766 - mae: 243.375 - ETA: 0s - loss: 242.2383 - mae: 242.737 - ETA: 0s - loss: 241.9649 - mae: 242.464 - ETA: 0s - loss: 242.6617 - mae: 243.160 - ETA: 0s - loss: 245.2848 - mae: 245.784 - ETA: 0s - loss: 246.6850 - mae: 247.184 - ETA: 0s - loss: 247.2272 - mae: 247.726 - ETA: 0s - loss: 246.9577 - mae: 247.457 - ETA: 0s - loss: 246.9871 - mae: 247.486 - ETA: 0s - loss: 248.7334 - mae: 249.232 - ETA: 0s - loss: 247.3515 - mae: 247.850 - ETA: 0s - loss: 246.6326 - mae: 247.131 - 1s 40ms/step - loss: 247.4818 - mae: 247.9811
Epoch 46/100
34/34 [==============================] - ETA: 0s - loss: 231.4669 - mae: 231.966 - ETA: 0s - loss: 244.6356 - mae: 245.134 - ETA: 0s - loss: 247.0056 - mae: 247.504 - ETA: 0s - loss: 245

34/34 [==============================] - ETA: 0s - loss: 232.2589 - mae: 232.758 - ETA: 0s - loss: 225.0720 - mae: 225.570 - ETA: 1s - loss: 221.9934 - mae: 222.492 - ETA: 1s - loss: 222.3532 - mae: 222.852 - ETA: 1s - loss: 219.8152 - mae: 220.314 - ETA: 0s - loss: 221.4055 - mae: 221.904 - ETA: 0s - loss: 220.2733 - mae: 220.772 - ETA: 0s - loss: 220.2684 - mae: 220.767 - ETA: 0s - loss: 219.6989 - mae: 220.198 - ETA: 0s - loss: 220.4698 - mae: 220.968 - ETA: 0s - loss: 221.4168 - mae: 221.915 - ETA: 0s - loss: 221.5858 - mae: 222.084 - ETA: 0s - loss: 223.2345 - mae: 223.733 - ETA: 0s - loss: 224.0358 - mae: 224.534 - ETA: 0s - loss: 224.3047 - mae: 224.803 - ETA: 0s - loss: 224.3336 - mae: 224.832 - ETA: 0s - loss: 223.9641 - mae: 224.463 - ETA: 0s - loss: 222.9568 - mae: 223.456 - 2s 45ms/step - loss: 222.0947 - mae: 222.5940
Epoch 15/100
34/34 [==============================] - ETA: 0s - loss: 215.1921 - mae: 215.691 - ETA: 0s - loss: 238.9223 - mae: 239.422 - ETA: 1s - loss: 225

In [11]:
week_weekdiff_recording

Model     Run0     Run1  \
0  <tensorflow.python.keras.engine.sequential.Seq... 248.9244 249.1033   
1  <tensorflow.python.keras.engine.sequential.Seq... 248.7319 248.6426   
2  <tensorflow.python.keras.engine.sequential.Seq... 248.6863 248.2279   
3  <tensorflow.python.keras.engine.sequential.Seq... 248.8962 248.6312   

      Run2     Run3     Run4     Run5     Run6     Run7     Run8     Run9  \
0 248.8627 248.1315 247.5275 247.1509 246.5082 247.1207 247.8306 247.4617   
1 247.2892 244.4161 244.2672 244.1785 239.5166 240.0367 239.0627 239.6445   
2 246.9807 243.8723 242.9384 242.5827 241.4952 235.1141 226.1939 223.5034   
3 247.2123 244.7091 244.7778 244.3420 242.4310 242.1876 241.0281 240.0188   

     Run10    Run11    Run12    Run13    Run14    Run15    Run16    Run17  \
0 247.3426 247.8568 247.5820 249.0939 247.6466 247.4135 248.2275 248.5882   
1 238.3562 236.5035 236.7834 236.5539 235.9904 235.3439 229.5483 231.1167   
2 222.5459 223.7137 227.7214 226.0802 227.6467 230.1185 232.9472 228.7407   
3 239.2534 239.4025 239.4090 237.5686 237.3921 237.6528 233.9478 233.3131   

     Run18    Run19    Run20    Run21    Run22    Run23    Run24    Run25  \
0 250.7081 251.5236 251.5277 251.6477 251.4556 251.4343 251.4822 251.4687   
1 230.1542 233.1428 230.8073 230.3293 229.8468 229.4466 228.7651 226.6738   
2 229.1100 229.7140 228.1664 226.7472 228.8501 237.6500 239.0345 237.1601   
3 233.2863 237.1333 235.6299 234.1928 232.3116 235.2128 233.6755 233.0320   

     Run26    Run27    Run28    Run29    Run30    Run31    Run32    Run33  \
0 251.4001 251.4778 251.4900 251.3981 251.4511 251.4056 251.4557 251.4330   
1 225.1579 224.5652 223.4565 227.1017 227.0478 228.5943 224.1949 226.5119   
2 230.7148 234.5848 235.0927 240.4682 240.9838 243.8047 249.6022 251.4576   
3 232.3975 230.8193 231.9635 232.5625 230.3620 232.9474 230.4356 230.6206   

     Run34    Run35    Run36    Run37    Run38    Run39    Run40    Run41  \
0 251.3720 251.4380 251.3823 251.4124 251.3963 251.4591 251.4682 251.4367   
1 224.3938 221.5015 223.8080 223.8719 220.2649 221.1557 219.5559 218.5339   
2 251.1202 250.4424 250.5493 250.0898 251.1364 251.1089 251.3751 251.1445   
3 231.5572 228.8428 228.8742 227.4785 225.0036 225.0141 225.1819 223.0439   

     Run42    Run43    Run44    Run45    Run46    Run47    Run48    Run49  \
0 251.4233 251.4770 251.4900 251.4542 251.4715 251.4129 251.4679 251.3661   
1 218.2727 221.3309 217.5041 218.7107 218.4136 215.4631 216.5644 221.6488   
2 250.8591 250.9260 250.8943 250.9313 250.9190 250.4995 250.5093 250.3029   
3 222.5871 223.4787 223.9346 224.9821 223.4533 226.9770 224.9074 224.1713   

     Run50    Run51    Run52    Run53    Run54    Run55    Run56    Run57  \
0 251.3916 251.3817 251.4511 251.4618 251.4271 251.4244 251.3550 251.3552   
1 223.7332 230.5989 221.1928 239.1455 225.9382 217.9857 216.0863 215.5845   
2 250.3400 250.3570 249.5637 250.6299 250.3210 249.9838 250.4157 249.9183   
3 228.8598 227.1606 222.2779 221.0077 221.9428 221.7913 222.3817 226.5851   

     Run58    Run59    Run60    Run61    Run62    Run63    Run64    Run65  \
0 251.4684 251.4353 251.4156 251.4649 251.3971 251.4215 251.4050 251.4895   
1 216.1338 215.9114 214.9292 215.5335 216.9462 217.2796 216.9210 218.6306   
2 249.6373 249.8888 249.7085 249.6292 249.4858 249.5532 249.4422 248.6252   
3 224.6538 223.1986 221.4389 224.0742 225.4587 223.4917 224.4045 224.0996   

     Run66    Run67    Run68    Run69    Run70    Run71    Run72    Run73  
0 251.4548 251.5591 251.4136 251.4310 251.4358 251.4397 251.3350 251.4604  
1 215.1434 217.1332 215.9483 217.9974 214.5361 213.9675 212.9027 212.3178  
2 249.1803 248.9536 250.4445 248.5817 248.0400 248.2648 247.8278 247.1909  
3 225.4717 223.0316 223.5320 224.0410 223.6566 222.8741 221.5996 224.0759

In [13]:
week_weekdiff_recording.to_csv('KerasResultsWeekWeekDiff02012021.csv')